*Internal Note:* 

- *The following is a tutorial template to be used by PO.DAAC staff when developing end-user tutorials.*
- *Copy this template and edit to create your notebook, keeping as many key elements as appropriate.*
- *DO NOT modify this template to create a tutorial. If you wish to make suggestions to improve the template please submit a PR and tag Catalina Oaida Taglialatela (ScienceCat18)*

> From the PO.DAAC Cookbook, to access the GitHub version of the notebook, follow [this link](insert link to notebook).

# SWOT Hydro Science Application Tutorial
#### *Authors: Cerbelaud A., Wade J., Jet Propulsion Laboratory - Caltech*

## Summary

_[Add summary/tutorial description here]_

## Requirements

### 1. Compute environment 
*internal note (remove this note in final tutorial): keep one or both of these Req 1 depending on environment required to run the noteook*

This tutorial can be run in the following environments:
- **AWS instance running in us-west-2**: NASA Earthdata Cloud data in S3 can be directly accessed via temporary credentials; this access is limited to requests made within the US West (Oregon) (code: `us-west-2`) AWS region.
- **Local compute environment** e.g. laptop, server: this tutorial can be run on your local machine

### 2. Earthdata Login

An Earthdata Login account is required to access data, as well as discover restricted data, from the NASA Earthdata system. Thus, to access NASA data, you need Earthdata Login. Please visit https://urs.earthdata.nasa.gov to register and manage your Earthdata Login account. This account is free to create and only takes a moment to set up.

### 3. Additional Requirements

Any other requirements needed for reproducing this tutorial.

## Learning Objectives
- enter objective 
- enter objective 
- ...

------

## Import Packages

In [2]:
import glob
import os
import requests
import s3fs
import fiona
import netCDF4 as nc
import h5netcdf
import xarray as xr
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import hvplot.xarray
import earthaccess
from earthaccess import Auth, DataCollections, DataGranules, Store

## Authenticate
Authenticate your Earthdata Login (EDL) information using the `earthaccess` python package as follows:

In [3]:
auth = earthaccess.login() # Login with your EDL credentials if asked

EARTHDATA_USERNAME and EARTHDATA_PASSWORD are not set in the current environment, try setting them or use a different strategy (netrc, interactive)
No .netrc found in /home/jovyan


Enter your Earthdata Login username:  jswade
Enter your Earthdata password:  ········


You're now authenticated with NASA Earthdata Login
Using token with expiration date: 03/16/2024
Using user provided credentials for EDL


#### Search for the data of interest

In [26]:
#Retrieves granule from the day we want, in this case by passing to `earthdata.search_data` function the data collection shortname, temporal bounds, and for restricted data one must specify the search count
# river_results = earthaccess.search_data(short_name = 'SWOT_L2_HR_RIVERSP_1.1', 
#                                         temporal = ('2023-04-08 00:00:00', '2023-04-22 23:59:59'),
#                                         granule_name = '*Reach*_009_NA*') # here we filter by Reach files (not node), pass #13 and continent code=NA

river_results = earthaccess.search_data(short_name = 'SWOT_L2_HR_RIVERSP_1.1', 
                                        temporal = ('2023-04-08 00:00:00', '2023-04-08 23:59:59'),
                                        granule_name = '*Reach*_009_NA*') # here we filter by Reach files (not node), pass #9 and continent code=NA

Granules found: 1


#### Set up an `s3fs` session for Direct Cloud Access
`s3fs` sessions are used for authenticated access to s3 bucket and allows for typical file-system style operations. Below we create session by passing in the data access information.

In [27]:
fs_s3 = earthaccess.get_s3fs_session(results=river_results)

#### Create Fiona session to work with zip and embedded shapefiles in the AWS Cloud
The native format for this data is a **.zip** file, and we want the **.shp** file within the .zip file, so we will create a Fiona AWS session using the credentials from setting up the s3fs session above to access the shapefiles within the zip files. If we don't do this, the alternative would be to download the data to the cloud environment (e.g. EC2 instance, user S3 bucket) and extract the .zip file there.

In [28]:
fiona_session=fiona.session.AWSSession(
        aws_access_key_id=fs_s3.storage_options["key"],
        aws_secret_access_key=fs_s3.storage_options["secret"],
        aws_session_token=fs_s3.storage_options["token"]
    )

In [29]:
# Initialize list to shp files
SWOT_HR_shps = []

# Loop through queried granules
for j in range(0,len(river_results)):
    
    # Get the link for each zip file
    river_link = earthaccess.results.DataGranule.data_links(river_results[j], access='direct')[0]
    
    # We use the zip+ prefix so fiona knows that we are operating on a zip file
    river_shp_url = f"zip+{river_link}"
    
    # Read shapefile
    with fiona.Env(session=fiona_session):
        SWOT_HR_shps.append(gpd.read_file(river_shp_url)) 

In [30]:
# Combine granules from time steps into one dataframe
SWOT_HR_df = gpd.GeoDataFrame(pd.concat(SWOT_HR_shps, ignore_index=True))

# Sort dataframe by reach_id
SWOT_HR_df = SWOT_HR_df.sort_values(['reach_id', 'time'])

In [144]:
for i in range(0,len(SWOT_HR_df)):
    print(SWOT_HR_df.columns[i])

reach_id
time
time_tai
time_str
p_lat
p_lon
river_name
wse
wse_u
wse_r_u
wse_c
wse_c_u
slope
slope_u
slope_r_u
slope2
slope2_u
slope2_r_u
width
width_u
width_c
width_c_u
area_total
area_tot_u
area_detct
area_det_u
area_wse
d_x_area
d_x_area_u
layovr_val
node_dist
loc_offset
xtrk_dist
dschg_c
dschg_c_u
dschg_csf
dschg_c_q
dschg_gc
dschg_gc_u
dschg_gcsf
dschg_gc_q
dschg_m
dschg_m_u
dschg_msf
dschg_m_q
dschg_gm
dschg_gm_u
dschg_gmsf
dschg_gm_q
dschg_b
dschg_b_u
dschg_bsf
dschg_b_q
dschg_gb
dschg_gb_u
dschg_gbsf
dschg_gb_q
dschg_h
dschg_h_u
dschg_hsf
dschg_h_q
dschg_gh
dschg_gh_u
dschg_ghsf
dschg_gh_q
dschg_o
dschg_o_u
dschg_osf
dschg_o_q
dschg_go
dschg_go_u
dschg_gosf
dschg_go_q
dschg_s
dschg_s_u
dschg_ssf
dschg_s_q
dschg_gs
dschg_gs_u
dschg_gssf
dschg_gs_q
dschg_i
dschg_i_u
dschg_isf
dschg_i_q
dschg_gi
dschg_gi_u
dschg_gisf
dschg_gi_q
dschg_q_b
dschg_gq_b
reach_q
reach_q_b
dark_frac
ice_clim_f
ice_dyn_f
partial_f
n_good_nod
obs_frac_n
xovr_cal_q
geoid_hght
geoid_slop
solid_tide
load_tide

IndexError: index 127 is out of bounds for axis 0 with size 127

In [147]:
x = SWOT_HR_df.iloc[:,np.r_[0:8,112,113,126]]
x.explore()


In [108]:
SWOT_HR_df[SWOT_HR_df.reach_id == "73120000131"]

reach_id          time      time_tai              time_str      p_lat  \
527  73120000131  7.342413e+08  7.342413e+08  2023-04-08T03:54:40Z  42.150023   

         p_lon                          river_name      wse    wse_u  wse_r_u  \
527 -72.611327  Connecticut River; Westfield River  15.5895  0.53756  0.52997   

     ...  p_wid_var  p_n_nodes  p_dist_out     p_length         p_maf  \
527  ...   3330.789         91  151626.309  18201.09844 -1.000000e+12   

     p_dam_id  p_n_ch_max  p_n_ch_mod  p_low_slp  \
527         0           2           1          0   

                                              geometry  
527  LINESTRING (-72.58355 42.08302, -72.58318 42.0...  

[1 rows x 127 columns]

#### Let's try to filter our river of interest by the `river_name` field

This isn't always reliable, as you can see in the plot of the Connecticut River below. Filtering by river name alone can include unwanted tributaries.

In [122]:
# Filter dataframe by river name of interest: 'Connecticut River'
# Note: Some rivers have multiple names, hence using the `contains` function
SWOT_sel_riv = SWOT_HR_df[SWOT_HR_df.river_name.str.contains("Connecticut River")]

# Plot geopandas dataframe with 'explore'
SWOT_sel_riv.explore()

#### Trace reaches downstream of starting reach using `rch_id_dn` field

In [123]:
# Format rch_id_dn for dictionary. Rch_id_dn allows for multiple downstream reaches to be stored
rch_id_dn = [[x.strip() for x in SWOT_HR_df.rch_id_dn[j].split(',')] for j in range(0,len(SWOT_HR_df.rch_id_dn))]

# Create lookup dictionary for river network topology: Downstream
rch_dn_dict = {SWOT_HR_df.reach_id[i]: rch_id_dn[i] for i in range(len(SWOT_HR_df))}

In [138]:
# Set starting reach_id: Headwaters of the Connecticut River
rch_dn_st = '73120000691'

# Initialize list to store downstream reaches, including starting reach
rch_dn_list = [rch_dn_st]

# Retrieve first downstream id of starting reach and add to list
rch_dn_next = rch_dn_dict[rch_dn_st][0]

# Trace next downstream reach until no reaches remaining
while rch_dn_next != 'no_data':
    
    # Add reach to list if value isn't 'no_data
    if rch_dn_next != 'no_data':
        rch_dn_list.append(rch_dn_next)
    
    # Recursively retrieve first downstream id of next reach
    # Catch error if reach isn't in downloaded data
    try:
        rch_dn_next = rch_dn_dict[rch_dn_next][0]
    except:
        break

In [140]:
# Filter downloaded data by traced reaches
SWOT_dn_trace = SWOT_HR_df[SWOT_HR_df.reach_id.isin(rch_dn_list)]

SWOT_dn_trace.explore()

#### Trace reaches upstream of starting reach using `rch_id_up` field

In [151]:
# Format rch_id_up for dictionary. Rch_id_up allows for multiple upstream reaches to be stored
rch_id_up = [[x.strip() for x in SWOT_HR_df.rch_id_up[j].split(',')] for j in range(0,len(SWOT_HR_df.rch_id_up))]

# Create lookup dictionary for river network topology: Upstream
rch_up_dict = {SWOT_HR_df.reach_id[i]: rch_id_up[i] for i in range(len(SWOT_HR_df))}

In [162]:
# Set starting reach_id: Outlet of the Connecticut River
rch_up_st = '73120000013'

# Initialize list to store upstream reaches, including starting reach
rch_up_list = [rch_up_st]

# Retrieve first upstream id of starting reach and add to list, removing 'no_data' values
rch_up_next = [x for x in rch_up_dict[rch_up_st] if 'no_data' not in x] 



rch_up_next

['73120000021']

In [157]:
rch_up_next[1]

'no_data'